## 作业1.提取副教授信息

In [1]:
import re
import requests
import pandas as pd
from parsel import Selector

In [2]:
# 定义浏览器请求头
headers = {
    'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_5)'
                  ' AppleWebKit/537.36 (KHTML, like Gecko) Chrome/75.0.3770.90 Safari/537.36'
}

In [22]:
def get_teach_info(link):
    """
    获取教师信息
    :param link:
    :return:
    """

    response = requests.get(link, headers=headers)
    text = response.content.decode('utf-8')
    html = Selector(text)

    name = html.xpath('//span[contains(text(), "姓")]/../../following-sibling::span/text() | //span[contains(text(), "姓　　名")]/../following-sibling::span/text() | //span[contains(text(), "Name")]/text() | //strong[contains(text(), "姓")]/../text() | //span[contains(text(), "姓　　名：")]/text() | //strong[contains(text(), "姓")]/../text()').extract_first('').strip('：')
    name = re.sub(r'\s', '', name)
    name = name.split('：')[-1]
    if name.startswith('Name:'):
        name = name.split(':')[-1]

    gender = html.xpath('//strong[contains(text(), "性")]/../text() | //span[contains(text(), "性　别")]/../following-sibling::span/text() | //span[contains(text(), "性　　别")]/../following-sibling::span/text() | //span[contains(text(), "Sex")]/text() | //strong[contains(text(), "性")]/../text() | //span[contains(text(), "性　　别：")]/text()').extract_first('').strip('：')
    gender = gender.split('：')[-1]
    if gender.startswith('Sex:'):
        gender = gender.split(':')[-1]

    politics_status = html.xpath('//strong[contains(text(), "政治")]/../text() | //span[contains(text(), "政治面貌")]/../following-sibling::span/text() | //strong[contains(text(), "政治")]/../text()').extract_first('').strip('：')
    graduate_school = html.xpath('//span[contains(text(), "毕业院校：")]/text() | //span[contains(text(), "毕业院校")]/../following-sibling::span[last()]/text() | //strong[contains(text(), "毕业院校")]/../text() | //span[contains(text(), "毕业院校")]/../following-sibling::span/text() | //span[contains(text(), "Graduated")]/text() | //strong[contains(text(), "毕业院校")]/../text()').extract_first('').strip('：')
    graduate_school = graduate_school.split('：')[-1]
    if graduate_school.startswith('Graduated:'):
        graduate_school = graduate_school.split(':')[-1]

    if graduate_school == '':
        graduate_school = html.xpath('//span[contains(text(), "毕业院校")]/../following-sibling::span[2]/text()').extract_first()

    contact_way = html.xpath('//span[contains(text(), "邮")]/text() | //p[contains(text(), "邮")]/text() | //strong[contains(text(), "邮")]/../text() | //span[contains(text(), "-Mail:")]/../text() | //span[contains(text(), "联系")]/../../following-sibling::span//text() | //span[contains(text(), "联系")]/../following-sibling::span//text() | //span[contains(text(), "Email")]/following-sibling::a/span/text() | //strong[contains(text(), "邮")]/../text() | //span[contains(text(), "邮")]/../following-sibling::span/text()').extract()
    contact_way = ''.join(contact_way).strip('：')

    contact_way = contact_way.split('：')[-1]
    contact_way = contact_way.split('年')[0]

    if name == '王金佑':
        pass
        # print(response.text)

    data = dict(
        name=name,
        gender=gender,
        politics_status=politics_status,
        graduate_school=graduate_school,
        contact_way=contact_way
    )
    return data


In [4]:
def get_teach_link(page):
    """
    获取教师链接
    :return:
    """
    url = f'http://finance.jxufe.edu.cn/news-list-fujiaoshou-{page}.html'

    response = requests.get(url, headers=headers)

    html = Selector(response.text)

    links = html.xpath('//div[@class="bd_listabc"]/ul/li/div[1]/a/@href').extract()

    data_list = []
    for link in links:
        trach_info = get_teach_info(link)
        data_list.append(trach_info)

    return data_list


In [18]:
def get_all_info():

    data_list1 = get_teach_link(1)
    data_list2 = get_teach_link(2)

    all_info = data_list1 + data_list2

    columns = ['name', 'gender', 'politics_status', 'graduate_school', 'contact_way']

    teach_df = pd.DataFrame(all_info, columns=columns)

    return teach_df

In [23]:
teach_df = get_all_info()

In [24]:
teach_df

name gender politics_status  \
0                 杜江泽      男            中共党员   
1   BadarNadeemAshraf   Male                   
2                 胡少勇      男            中共党员   
3                 胡志军      男            中共党员   
4                  李英      女              群众   
5                 李思敏      男            中共党员   
6                 闵晓平      男         中国民主促进会   
7                  潜力      男                   
8                 舒海棠      女            中共党员   
9                 谭英贤      男            中共党员   
10                王金佑      男                   
11                吴伟军      男            中共党员   
12                徐海云      男            中共党员   
13                赵玉洁      女                   
14                钟小林      男            中共党员   
15                曾鸿志      男              党员   
16                曾莉华      女              群众   
17                邹朋飞      男              群众   

                                   graduate_school           contact_way  
0                                           香港城市大学      citysnail@qq.com  
1    Huazhong University of Science and Technology    badar@jxufe.edu.cn  
2                                           华东师范大学       45022251@qq.com  
3                                           上海财经大学                        
4                                           东北财经大学   liying8881@sina.com  
5                                             None  jxcdzqtzxlsm@126.com  
6                                           上海交通大学      mxptiger@163.com  
7                                           西安交通大学     1752192559@qq.com  
8                                           江西财经大学      744289565@qq.com  
9                                             湖南大学        yxtan6@163.com  
10                                          中国人民大学    wongchange@163.com  
11                                          江西财经大学       wwj1277@163.com  
12                                        中南财经政法大学  haiyunxjxufe@126.com  
13                                            复旦大学      verg0601@126.com  
14                                          江西财经大学       zxl6588@163.com  
15                                            天津大学       18409495@qq.com  
16                                          江西财经大学       jxcdzlh@163.com  
17                                            暨南大学    Pengfeizou@163.com